## Investigate "collision protection volume" concept

In [1]:
%matplotlib inline
%reload_ext autoreload
%autoreload

In [2]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os

import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
import plotly.io as pio

### Load data
Load data from the `./data/interim/` folder and parse into `pandas` dataframes.

In [83]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_profile_features = df_from_csv('profile_features.csv', index_col=[0])

impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }

twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}

print('Done!')

Importing profiles.csv


C:\Users\z5189959\AppData\Local\Continuum\anaconda3\lib\site-packages\numpy\lib\arraysetops.py:472: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



Importing profile_features.csv
Importing impacts_forecasted_foreshore_slope_sto06.csv
Importing impacts_forecasted_mean_slope_sto06.csv
Importing impacts_observed.csv
Importing twl_foreshore_slope_sto06.csv
Importing twl_mean_slope_sto06.csv
Done!


Lets define a function to calculate the "collision protection volume" based on prestorm profiles.

In [4]:
from shapely.geometry import Point, LineString, Polygon

def collision_protection_vol(x,z, d_low_x, d_low_z, lower_z, angle):
    # First, get the bounding line strings of our protection volume
    lower_line = LineString([Point(min(x), lower_z), Point(max(x), lower_z)])
    profile_line = LineString([Point(x_coord, z_coord) for x_coord, z_coord in zip(x,z) 
                               if all([not np.isnan(x_coord), not np.isnan(z_coord)])])
    slope_line = LineString([Point(d_low_x, d_low_z), 
                             Point(max(x), d_low_z - max(x) * np.sin(np.deg2rad(angle)))])

    # Work out where our lower line and slope line intersect
    lower_profile_intersection = lower_line.intersection(profile_line)
    d_protected_intersection = lower_line.intersection(slope_line)
    
    # Define the perimeter of the protection area
    profile_protected = LineString([Point(x_coord, z_coord) for x_coord, z_coord 
                                   in zip(profile_line.xy[0],profile_line.xy[1]) 
                                   if d_low_x < x_coord < lower_profile_intersection.xy[0][0]] 
                                   + [lower_profile_intersection]
                                   + [d_protected_intersection]
                                   + [Point(d_low_x, d_low_z)])
    
    # Convert to polygon and return the area (m3/m)
    protection_area_poly = Polygon(profile_protected)
    protection_area_vol = protection_area_poly.area
    return protection_area_vol

site_id = 'NARRA0018'
profile_type = 'prestorm'
query = "site_id == '{}' and profile_type == '{}'".format(site_id, profile_type)
prestorm_profile = df_profiles.query(query)
profile_features = df_profile_features.query(query)

x = prestorm_profile.index.get_level_values('x')
z = prestorm_profile.z
d_low_x = profile_features.dune_toe_x.tolist()[0]
d_low_z = profile_features.dune_toe_z.tolist()[0]
angle = 60  # degrees from the horizontal
lower_z = 0.5 # from mhw

vol = collision_protection_vol(x,z, d_low_x, d_low_z, lower_z, angle)

In [58]:
from datetime import timedelta

def wl_time(t, wl, z_lower, z_upper):
    """
    Returns the amount of time the water level is between two elevations.
    """
    df_wl = pd.DataFrame.from_records([(t_val, R2_val) for t_val, R2_val in zip(t,R2)], columns=['datetime','wl'])
    df_wl.set_index(pd.DatetimeIndex(df_wl['datetime']),inplace=True)
    df_wl.drop(columns=['datetime'], inplace=True)
    
    # Assumes that each record is one hour... probably need to check this
    hours = len(df_wl.query('{} < wl < {}'.format(z_lower, z_upper)))
    return timedelta(hours=hours)

def wave_power(t, wl, z_lower, z_upper, Hs0, Tp):
    """
    Returns the cumulative wave power when the water level is between two elevations.
    """
    df_wl = pd.DataFrame.from_records([(t_val, R2_val,Hs0_val,Tp_val) for t_val, R2_val,Hs0_val,Tp_val in zip(t,R2,Hs0,Tp)], columns=['datetime','wl', 'Hs0','Tp'])
    df_wl.set_index(pd.DatetimeIndex(df_wl['datetime']),inplace=True)
    df_wl.drop(columns=['datetime'], inplace=True)
    
    # Assumes that each record is one hour... probably need to check this
    rho = 1025 # kg/m3
    g = 9.8 # m/s2
    df_wl_times = df_wl.query('{} < wl < {}'.format(z_lower, z_upper))
    power = rho * g ** 2 / 64 / np.pi * df_wl_times.Hs0 ** 2 * df_wl_times.Tp
    return power.sum()

df_twl = twls['forecasted']['mean_slope_sto06']
df_twl_site = df_twl.query("site_id == '{}'".format(site_id))

R2 = df_twl_site.R2.tolist()
t = df_twl_site.index.get_level_values('datetime')
z_lower = 0.5
z_upper = d_low_z

exposed_time = wl_time(t, R2, z_lower,z_upper)

Hs0 = df_twl.Hs0.tolist()
Tp = df_twl.Tp.tolist()
wave_p = wave_power(t, R2, z_lower,z_upper,Hs0, Tp)


In [59]:
wave_p

8554715.596323118

In [21]:
def dune_toe_elevation_change(site_id, df_profile_features):
    query = "site_id == '{}'".format(site_id)
    profile_features = df_profile_features.query(query)
    prestorm_dune_toe_z = profile_features.query("profile_type=='prestorm'").dune_toe_z.tolist()[0]
    poststorm_dune_toe_z = profile_features.query("profile_type=='poststorm'").dune_toe_z.tolist()[0]
    return prestorm_dune_toe_z - poststorm_dune_toe_z

toe_ele_change = dune_toe_elevation_change("NARRA0018", df_profile_features)

In [92]:
vols = []
exposed_times = []
toe_ele_changes = []
wave_powers = []

# Get site ids where we observed collision
observed_site_ids = impacts['observed'].query("storm_regime=='collision'").index.get_level_values('site_id').unique()

# Get site ids where we forecast swash
forecasted_site_ids = impacts['forecasted']['mean_slope_sto06'].query("storm_regime=='swash'").index.get_level_values('site_id').unique()

site_ids = set(observed_site_ids).intersection(set(forecasted_site_ids))

# Calculate for each site

for n, site_id in enumerate(site_ids):
    
    if n%20 ==0:
        print('{} of {}'.format(n, len(site_ids)))
    
    try:
        query = "site_id == '{}' and profile_type == '{}'".format(site_id, 'prestorm')
        prestorm_profile = df_profiles.query(query)
        profile_features = df_profile_features.query(query)

        vol = collision_protection_vol(x = prestorm_profile.index.get_level_values('x'),
                                       z = prestorm_profile.z,
                                       d_low_x = profile_features.dune_toe_x.tolist()[0],
                                       d_low_z = profile_features.dune_toe_z.tolist()[0],
                                       lower_z = profile_features.dune_toe_z.tolist()[0] - 2, # from mhw
                                       angle = 60,  # degrees from the horizontal
                                      )

        df_twl = twls['forecasted']['mean_slope_sto06']
        df_twl_site = df_twl.query("site_id == '{}'".format(site_id))

        exposed_time = wl_time(t = df_twl_site.index.get_level_values('datetime'),
                               wl = df_twl_site.R2.tolist(),
                               z_lower = profile_features.dune_toe_z.tolist()[0] -2,
                               z_upper = profile_features.dune_toe_z.tolist()[0],
                              )

        
        power = wave_power(t = df_twl_site.index.get_level_values('datetime'),
                           wl = df_twl_site.R2.tolist(),
                           z_lower = profile_features.dune_toe_z.tolist()[0] -2,
                           z_upper = profile_features.dune_toe_z.tolist()[0],
                           Hs0=df_twl_site.Hs0.tolist(),
                           Tp=df_twl_site.Tp.tolist())
        
        toe_ele_change = dune_toe_elevation_change(site_id, df_profile_features)
    except:
        continue

    vols.append(vol)
    exposed_times.append(exposed_time)
    toe_ele_changes.append(toe_ele_change)
    wave_powers.append(power)
#     if n>100:
#         break

    



0 of 204
20 of 204
40 of 204
60 of 204
80 of 204
100 of 204
120 of 204
140 of 204
160 of 204
180 of 204
200 of 204


[0.0,
 62.0,
 35.0,
 53.0,
 4.0,
 41.0,
 31.0,
 98.0,
 17.0,
 103.0,
 81.0,
 1.0,
 31.0,
 0.0,
 24.0,
 35.0,
 67.0,
 53.0,
 77.0,
 130.0,
 66.0,
 89.0,
 31.0,
 13.0,
 41.0,
 118.0,
 0.0,
 29.0,
 82.0,
 52.0,
 84.0,
 31.0,
 2.0,
 43.0,
 84.0,
 421.0,
 29.0,
 22.0,
 54.0,
 150.0,
 115.0,
 46.0,
 29.0,
 86.0,
 103.0,
 82.0,
 77.0,
 50.0,
 104.0,
 81.0,
 67.0,
 81.0,
 141.0,
 64.0,
 17.0,
 95.0,
 46.0,
 80.0,
 77.0,
 4.0,
 159.0,
 115.0,
 33.0,
 13.0,
 46.0,
 110.0,
 162.0,
 16.0,
 77.0,
 77.0,
 86.0,
 46.0,
 6.0,
 42.0,
 77.0,
 89.0,
 29.0,
 172.0,
 68.0,
 204.0,
 8.0,
 13.0,
 78.0,
 0.0,
 81.0,
 156.0,
 57.0,
 0.0,
 62.0,
 46.0,
 37.0,
 52.0,
 310.0,
 287.0,
 4.0,
 89.0,
 2.0,
 22.0,
 31.0,
 20.0,
 45.0,
 54.0,
 46.0,
 43.0,
 0.0,
 89.0,
 122.0,
 5.0,
 46.0,
 24.0,
 0.0,
 77.0,
 51.0,
 0.0,
 43.0,
 53.0,
 151.0,
 52.0,
 29.0,
 103.0,
 35.0,
 68.0,
 17.0,
 29.0,
 34.0,
 211.0,
 55.0,
 85.0,
 21.0,
 14.0,
 103.0,
 227.0,
 208.0,
 78.0,
 43.0,
 17.0,
 104.0,
 50.0,
 37.0,
 54.0,
 78.0,
 349

In [104]:
trace1 = go.Scatter(
    x=[x.total_seconds() / 60 / 60 for x in exposed_times],
    y=vols,
    text = ['{}<br>{}'.format(ele, site_id) for ele,site_id in zip(toe_ele_changes,site_ids)],
    mode='markers',
    marker=dict(
        size=4,
#         color = [-1 if x<0 else 1 for x in toe_ele_changes],
        color =  toe_ele_changes,
#         color = wave_powers,
#         color = [x.total_seconds() / 60 / 60 for x in exposed_times],
        colorscale='Viridis',
        showscale=True
    ))

layout = go.Layout(
    title='Dune Collision Protection',
#     height=300,
#     legend=dict(font={'size': 10}),
#     margin=dict(t=50, b=50, l=50, r=20),
    xaxis=dict(
        title='Exposed time',
        autorange=True,
        showgrid=True,
        zeroline=True,
        showline=True,
    ),
    yaxis=dict(
        title='Collision protection volume',
        autorange=True,
        showgrid=True,
        zeroline=True,
        showline=True,
    ))

g_plot = go.FigureWidget(data=[trace1], layout=layout)
g_plot

FigureWidget({
    'data': [{'marker': {'color': [0.6740000000000004, -0.262, 0.5449999999999999,
                                   0.35399999999999965, 0.3929999999999998,
                                   0.35399999999999965, 0.6699999999999999,
                                   -0.22799999999999976, 1.0739999999999998,
                                   -0.125, 0.35199999999999987, 0.5299999999999998,
                                   0.4109999999999996, -0.1120000000000001,
                                   0.9180000000000001, 0.621, -0.3579999999999992,
                                   -0.20699999999999985, -0.48400000000000043,
                                   0.5430000000000001, -0.09600000000000053,
                                   -0.41700000000000026, 0.4340000000000006,
                                   0.7559999999999998, 0.8720000000000003,
                                   -0.5759999999999996, 0.5119999999999996,
                                   0.6440000000000001, 0.395, 0.09300000000000042,
                                   0.923, 0.4339999999999997, 0.5429999999999993,
                                   -0.09699999999999998, -0.20899999999999963,
                                   -0.8130000000000002, 0.706, 0.36399999999999944,
                                   0.34099999999999975, -0.08499999999999996,
                                   0.21799999999999953, 0.6240000000000006,
                                   -0.16700000000000026, -0.278,
                                   -0.5110000000000001, 0.726,
                                   -0.35199999999999987, 0.13100000000000023,
                                   -0.3440000000000003, 0.6760000000000002,
                                   -0.5719999999999996, -0.4980000000000002,
                                   -0.2020000000000004, 0.34199999999999964,
                                   0.41999999999999993, 0.5800000000000001,
                                   0.7200000000000002, 0.6230000000000002,
                                   -0.49100000000000055, 0.11499999999999977,
                                   -0.242, -0.6240000000000006, 0.9500000000000002,
                                   1.2479999999999998, 1.2889999999999997,
                                   0.021999999999999797, -0.3200000000000003,
                                   0.7829999999999999, -0.32899999999999974,
                                   0.3389999999999995, -0.01599999999999957,
                                   0.38399999999999945, -0.04599999999999982,
                                   0.4849999999999999, 0.02499999999999991,
                                   -0.7749999999999999, 0.617,
                                   -0.06500000000000039, 0.5589999999999997,
                                   -0.1299999999999999, -0.0040000000000000036,
                                   1.298, 0.05500000000000016, 0.9689999999999999,
                                   -0.28800000000000026, -0.09700000000000042,
                                   -0.03100000000000014, 0.7960000000000003,
                                   0.33599999999999985, 0.28900000000000015, 0.798,
                                   -0.05900000000000016, -0.0029999999999996696,
                                   -0.15399999999999991, 0.31999999999999984,
                                   -0.613, 0.2650000000000001, 0.258, 1.513,
                                   0.36199999999999966, 0.7849999999999997,
                                   -0.28900000000000015, 1.0290000000000004,
                                   0.8260000000000005, -0.03799999999999981,
                                   -0.21300000000000008, -0.492,
                                   1.6029999999999998, 0.5699999999999998,
                                   0.9300000000000002, 0.0389999999999997,
                                   -0.3110000000000004, 1.0070000000000001,
                                   0.11500000000000021